Todo in data
- Column names -> no space
- If a list is empty, serialise [] in the csv
- If a string is empty, serialise '' in the csv

In [1]:
import ast
from urllib.parse import urlparse
import tldextract

import pandas as pd
from sklearn.preprocessing import MultiLabelBinarizer


In [2]:
mlb = MultiLabelBinarizer()

In [3]:
# Notable Solid ORCID iDs for debug purposes
AM = '0000-0002-5193-7851'
PP = '0000-0002-8588-4196'


In [4]:
# Notable fake ORCID iDs for debug purposes
SCAFFOLD = '0000-0001-5004-7761'
WHATSAPP = '0000-0001-6997-9470'


In [5]:
df = pd.read_csv('../data/raw/initial_info_whole.tsv', sep='\t', header = 0,
                         dtype = {"orcid": pd.StringDtype(), 
                                  "claimed": bool, 
                                  "verifyed email": bool, 
                                  "verified primary email": bool,
                                  "given names": pd.StringDtype(),
                                  "family name": pd.StringDtype(),
                                  "biography": pd.StringDtype(),
                                  "other names": pd.StringDtype(),
                                  "researcher urls": pd.StringDtype(),
                                  "primary email": pd.StringDtype(),
                                  "other emails": pd.StringDtype(),
                                  "keywords": pd.StringDtype(),
                                  "eternal identifiers": pd.StringDtype(),
                                  "education": pd.StringDtype(),
                                  "employments": pd.StringDtype(),
                                  "number of works": pd.Int16Dtype(),
                                  "works source": pd.StringDtype()})

In [6]:
df.head(5)

orcid  claimed  verifyed email  verified primary email  \
0  0000-0001-5000-2053     True           False                   False   
1  0000-0001-5000-6548     True           False                   False   
2  0000-0001-5000-7962     True            True                    True   
3  0000-0001-5000-8586     True           False                   False   
4  0000-0001-5001-0256     True           False                   False   

  given names         family name biography other names researcher urls  \
0      Jorge   Jaramillo Sanchez       <NA>        <NA>            <NA>   
1     Wiseman            Bekelesi      <NA>        <NA>            <NA>   
2       ALICE            INDIMULI      <NA>        <NA>            <NA>   
3        shim              ji yun      <NA>        <NA>            <NA>   
4      Sandro          Caramaschi      <NA>        <NA>            <NA>   

  primary email other emails keywords external identifiers education  \
0          <NA>         <NA>     <NA>                  NaN      <NA>   
1          <NA>         <NA>     <NA>                  NaN      <NA>   
2          <NA>         <NA>     <NA>                  NaN      <NA>   
3          <NA>         <NA>     <NA>                  NaN      <NA>   
4          <NA>         <NA>     <NA>                  NaN      <NA>   

  employments  number of works works source  
0        <NA>                0         <NA>  
1        <NA>                0         <NA>  
2        <NA>                0         <NA>  
3        <NA>                0         <NA>  
4        <NA>                0         <NA>

In [7]:
df[df['orcid'] == AM]

orcid  claimed  verifyed email  verified primary email  \
8840413  0000-0002-5193-7851     True            True                    True   

        given names family name biography other names  \
8840413      Andrea    Mannocci      <NA>        <NA>   

                                           researcher urls  \
8840413  [["Personal website", "https://andremann.githu...   

                       primary email other emails  \
8840413  andrea.mannocci@isti.cnr.it         <NA>   

                                                  keywords  \
8840413  ["Data science ", "science of science", "schol...   

                          external identifiers  \
8840413  [["Scopus Author ID", "55233589900"]]   

                                                 education  \
8840413  [["Information engineering", "Ph.D.", "Univers...   

                                               employments  number of works  \
8840413  [["Research Associate", "Istituto di Scienza e...               37   

                                              works source  
8840413  ["Scopus - Elsevier", "Crossref Metadata Searc...

# Extracting works source

In [8]:
df['works source'] = df['works source'].fillna('[]').apply(lambda x: ast.literal_eval(x))

In [9]:
def extract_work_source(lst):
    extracted = []
    for s in lst:
        if 'Scopus - Elsevier' in s or 'Crossref' in s:
            extracted.append(s)
    return extracted

In [10]:
df['extracted_works_source'] = df['works source'].apply(lambda x: extract_work_source(x))

In [11]:
df = pd.concat([df, pd.DataFrame(mlb.fit_transform(df['extracted_works_source']), columns=mlb.classes_)], axis = 1)

In [12]:
df.drop(['works source', 'extracted_works_source'], axis=1, inplace=True)

In [13]:
df[df['orcid'] == AM]

orcid  claimed  verifyed email  verified primary email  \
8840413  0000-0002-5193-7851     True            True                    True   

        given names family name biography other names  \
8840413      Andrea    Mannocci      <NA>        <NA>   

                                           researcher urls  \
8840413  [["Personal website", "https://andremann.githu...   

                       primary email other emails  \
8840413  andrea.mannocci@isti.cnr.it         <NA>   

                                                  keywords  \
8840413  ["Data science ", "science of science", "schol...   

                          external identifiers  \
8840413  [["Scopus Author ID", "55233589900"]]   

                                                 education  \
8840413  [["Information engineering", "Ph.D.", "Univers...   

                                               employments  number of works  \
8840413  [["Research Associate", "Istituto di Scienza e...               37   

         Crossref  Crossref Metadata Search  Scopus - Elsevier  
8840413         1                         1                  1

# Education

In [14]:
df['education'] = df['education'].fillna('[]').apply(lambda x: ast.literal_eval(x))

In [15]:
df['n_education'] = df['education'].str.len()

In [16]:
df.drop('education', axis=1, inplace=True)

In [17]:
df[df['orcid'] == AM]

orcid  claimed  verifyed email  verified primary email  \
8840413  0000-0002-5193-7851     True            True                    True   

        given names family name biography other names  \
8840413      Andrea    Mannocci      <NA>        <NA>   

                                           researcher urls  \
8840413  [["Personal website", "https://andremann.githu...   

                       primary email other emails  \
8840413  andrea.mannocci@isti.cnr.it         <NA>   

                                                  keywords  \
8840413  ["Data science ", "science of science", "schol...   

                          external identifiers  \
8840413  [["Scopus Author ID", "55233589900"]]   

                                               employments  number of works  \
8840413  [["Research Associate", "Istituto di Scienza e...               37   

         Crossref  Crossref Metadata Search  Scopus - Elsevier  n_education  
8840413         1                         1                  1            4

# Employment

In [18]:
df['employments'] = df['employments'].fillna('[]').apply(lambda x: ast.literal_eval(x))

In [19]:
df['n_employments'] = df['employments'].str.len()

In [20]:
df.drop('employments', axis=1, inplace=True)

In [21]:
df[df['orcid'] == AM]

orcid  claimed  verifyed email  verified primary email  \
8840413  0000-0002-5193-7851     True            True                    True   

        given names family name biography other names  \
8840413      Andrea    Mannocci      <NA>        <NA>   

                                           researcher urls  \
8840413  [["Personal website", "https://andremann.githu...   

                       primary email other emails  \
8840413  andrea.mannocci@isti.cnr.it         <NA>   

                                                  keywords  \
8840413  ["Data science ", "science of science", "schol...   

                          external identifiers  number of works  Crossref  \
8840413  [["Scopus Author ID", "55233589900"]]               37         1   

         Crossref Metadata Search  Scopus - Elsevier  n_education  \
8840413                         1                  1            4   

         n_employments  
8840413              5

# External IDs

In [22]:
df['external identifiers'] = df['external identifiers'].fillna('[]').apply(lambda x: ast.literal_eval(x))

In [23]:
# def extract_ids(lst):
#     extracted = []
#     for id in lst:
#         extracted.append(id[0])
#     return extracted

In [24]:
# df['extracted_identifiers'] = df['external identifiers'].apply(lambda x: extract_ids(x))

In [25]:
# df = pd.concat([df, pd.DataFrame(mlb.fit_transform(df['extracted_identifiers']), columns=mlb.classes_)], axis = 1)

In [26]:
df['n_ext_ids'] = df['external identifiers'].str.len()

In [27]:
df.drop(['external identifiers'], axis=1, inplace=True)

In [28]:
df[df['orcid'] == AM]

orcid  claimed  verifyed email  verified primary email  \
8840413  0000-0002-5193-7851     True            True                    True   

        given names family name biography other names  \
8840413      Andrea    Mannocci      <NA>        <NA>   

                                           researcher urls  \
8840413  [["Personal website", "https://andremann.githu...   

                       primary email other emails  \
8840413  andrea.mannocci@isti.cnr.it         <NA>   

                                                  keywords  number of works  \
8840413  ["Data science ", "science of science", "schol...               37   

         Crossref  Crossref Metadata Search  Scopus - Elsevier  n_education  \
8840413         1                         1                  1            4   

         n_employments  n_ext_ids  
8840413              5          1

# Extracting email domains

In [29]:
df['primary email'] = df['primary email'].fillna('')
df['other emails'] = df['other emails'].fillna('[]').apply(lambda x: ast.literal_eval(x))

In [30]:
def extract_email_domains(row):
    domains = []
    if len(row['primary email']) > 0:
        domains.append(row['primary email'].split('@')[1])
    for email in row['other emails']:
        domains.append(email.split('@')[1])
    return domains

In [31]:
df['email_domains'] = df[['primary email','other emails']].apply(lambda row: extract_email_domains(row), axis=1)

In [32]:
df[df['email_domains'].str.len() != 0]['email_domains']

34          [seh.ox.ac.uk, bsg.ox.ac.uk]
47                         [foxmail.com]
103                     [fvtm.bu.edu.eg]
297                           [unipa.it]
299                            [nhs.net]
                        ...             
10746811             [gva.es, gmail.com]
10746850                  [cinvestav.mx]
10746920        [gmail.com, hotmail.com]
10746975                       [mail.ru]
10746988                        [ucm.es]
Name: email_domains, Length: 141118, dtype: object

In [ ]:
df = pd.concat([df, pd.DataFrame(mlb.fit_transform(df['email_domains']), columns=mlb.classes_)], axis = 1)

In [ ]:
df.drop(['primary email', 'other emails', 'email_domains'], axis=1, inplace=True)

In [ ]:
df[df['orcid'] == AM]

# Extracting URL domains

In [35]:
df['researcher urls'] = df['researcher urls'].fillna('[]').apply(lambda x: ast.literal_eval(x))

In [36]:
def extract_url_domains(lst):
    domains = []
    for e in lst:
        # e[0] is a string describing the url
        # e[1] is the url
        ext = tldextract.extract(e[1])
        domains.append(ext.registered_domain)
    return domains

In [37]:
df['url_domains'] = df['researcher urls'].apply(lambda lst: extract_url_domains(lst))

In [38]:
df[df['url_domains'].str.len() != 0]['url_domains']

5                           [researchgate.net]
14                      [tigerscaffolds.co.nz]
15                         [corticalbrain.com]
29                                   [cnpq.br]
30                                [sksahu.net]
                           ...                
10746945                          [telegra.ph]
10746950    [twitter.com, urbanfoodpolicy.com]
10746955                    [openlearning.com]
10746984                        [panaximco.vn]
10746987                       [swansea.ac.uk]
Name: url_domains, Length: 688572, dtype: object

In [ ]:
df = pd.concat([df, pd.DataFrame(mlb.fit_transform(df['url_domains']), columns=mlb.classes_)], axis = 1)

In [39]:
df.drop(['researcher urls', 'url_domains'], axis=1, inplace=True)

In [40]:
df[df['orcid'] == AM]

orcid  claimed  verifyed email  verified primary email  \
8840413  0000-0002-5193-7851     True            True                    True   

        given names family name biography other names  \
8840413      Andrea    Mannocci      <NA>        <NA>   

                                                  keywords  number of works  \
8840413  ["Data science ", "science of science", "schol...               37   

         Crossref  Crossref Metadata Search  Scopus - Elsevier  n_education  \
8840413         1                         1                  1            4   

         n_employments  n_ext_ids  email_domains  \
8840413              5          1  [isti.cnr.it]   

                                    url_domains  
8840413  [github.io, twitter.com, linkedin.com]

# Fixing keywords

In [18]:
df['keywords'] = df['keywords'].fillna('[]').apply(lambda x: ast.literal_eval(x))

Sometimes, different keywords are provided as a continuum (multiplexed in just one keyword). E.g.

In [19]:
df[df['orcid'] == PP]

orcid  claimed  verifyed email  verified primary email  \
9601705  0000-0002-8588-4196     True            True                    True   

        given names family name  \
9601705       Pedro    Príncipe   

                                                 biography  \
9601705  Pedro Príncipe is an information, documentatio...   

                                              other names researcher urls  \
9601705  ["Pedro Miguel de Oliveira Bento Pr\u00edncipe"]              []   

        primary email other emails  \
9601705                         []   

                                                  keywords  \
9601705  [open access, open science, libraries, reposit...   

                            external identifiers education  \
9601705  [["Ci\u00eancia ID", "C915-48B2-6C87"]]      <NA>   

                                               employments  number of works  \
9601705  [["Librarian / Project manager", "Universidade...                5   

                                              works source email_domains  \
9601705  ["CI\u00caNCIAVITAE", "Pedro Pr\u00edncipe", "...            []   

        url_domains  
9601705          []

In [20]:
def fix_keywords(lst):
    fixed = []
    for k in lst:
        split = k.split(',')
        fixed.extend(split)
    return fixed

In [21]:
test = ['open access, open science, libraries, repositories, social web,']
fix_keywords(test)

['open access',
 ' open science',
 ' libraries',
 ' repositories',
 ' social web',
 '']

In [22]:
df['fixed_keywords'] = df['keywords'].apply(lambda lst: fix_keywords(lst))

In [23]:
df[df['orcid'] == WHATSAPP]

orcid  claimed  verifyed email  verified primary email  \
9517099  0000-0001-6997-9470     True            True                    True   

        given names family name biography other names  \
9517099       other    whatsapp      <NA>        <NA>   

                                           researcher urls primary email  \
9517099  [[Otherwhatsapp, https://otherwhatsapp.com/], ...                 

        other emails                                           keywords  \
9517099           []  [Whatsapp GB, whatsapp gb 2020, whatsapp gb ba...   

        external identifiers education employments  number of works  \
9517099                  NaN      <NA>        <NA>                0   

        works source email_domains  \
9517099         <NA>            []   

                                               url_domains  \
9517099  [otherwhatsapp.com, im-creator.com, facebook.c...   

                                            fixed_keywords  
9517099  [Whatsapp GB, whatsapp gb 2020, whatsapp gb ba...

In [24]:
df.drop('keywords', axis=1, inplace=True)

orcid  claimed  verifyed email  \
0         0000-0001-5000-2053     True           False   
1         0000-0001-5000-6548     True           False   
2         0000-0001-5000-7962     True            True   
3         0000-0001-5000-8586     True           False   
4         0000-0001-5001-0256     True           False   
...                       ...      ...             ...   
10747035  0000-0003-4998-1551     True           False   
10747036  0000-0003-4998-4111     True           False   
10747037  0000-0003-4998-6045     True           False   
10747038  0000-0003-4998-8868     True            True   
10747039  0000-0003-4999-7916     True            True   

          verified primary email given names         family name biography  \
0                          False      Jorge   Jaramillo Sanchez       <NA>   
1                          False     Wiseman            Bekelesi      <NA>   
2                           True       ALICE            INDIMULI      <NA>   
3                          False        shim              ji yun      <NA>   
4                          False      Sandro          Caramaschi      <NA>   
...                          ...         ...                 ...       ...   
10747035                   False     Animesh               Ghosh      <NA>   
10747036                   False        Hawa             Liberna      <NA>   
10747037                   False      Tongyi                 Men      <NA>   
10747038                   False    Charldon              Wilken      <NA>   
10747039                    True  Tapas Bapu                B.R.      <NA>   

         other names researcher urls primary email other emails  \
0               <NA>              []                         []   
1               <NA>              []                         []   
2               <NA>              []                         []   
3               <NA>              []                         []   
4               <NA>              []                         []   
...              ...             ...           ...          ...   
10747035        <NA>              []                         []   
10747036        <NA>              []                         []   
10747037        <NA>              []                         []   
10747038        <NA>              []                         []   
10747039        <NA>              []                         []   

         external identifiers education employments  number of works  \
0                         NaN      <NA>        <NA>                0   
1                         NaN      <NA>        <NA>                0   
2                         NaN      <NA>        <NA>                0   
3                         NaN      <NA>        <NA>                0   
4                         NaN      <NA>        <NA>                0   
...                       ...       ...         ...              ...   
10747035                  NaN      <NA>        <NA>                0   
10747036                  NaN      <NA>        <NA>                0   
10747037                  NaN      <NA>        <NA>                0   
10747038                  NaN      <NA>        <NA>                0   
10747039                  NaN      <NA>        <NA>                0   

         works source email_domains url_domains fixed_keywords  
0                <NA>            []          []             []  
1                <NA>            []          []             []  
2                <NA>            []          []             []  
3                <NA>            []          []             []  
4                <NA>            []          []             []  
...               ...           ...         ...            ...  
10747035         <NA>            []          []             []  
10747036         <NA>            []          []             []  
10747037         <NA>            []          []             []  
10747038         <NA>            []          []             []  
10747

# Fixes for other columns with lists inside

In [27]:
# df['other names'] = df['other names'].apply(lambda x: ast.literal_eval(x))
# df['other emails'] = df['other emails'].fillna('[]').apply(lambda x: ast.literal_eval(x))
# df['researcher urls'] = df['researcher urls'].fillna('[]').apply(lambda x: ast.literal_eval(x))
# df['keywords'] = df['keywords'].fillna('[]').apply(lambda x: ast.literal_eval(x))
# df['education'] = df['education'].fillna('[]').apply(lambda x: ast.literal_eval(x))
# df['employments'] = df['employments'].fillna('[]').apply(lambda x: ast.literal_eval(x))
# df['external identifiers'] = df['external identifiers'].fillna('[]').apply(lambda x: ast.literal_eval(x))
# df['works source'] = df['works source'].fillna('[]').apply(lambda x: ast.literal_eval(x))

# Feature extraction

In [28]:
# df['email_encoding'] = mlb.fit_transform(df['email_domains'])
# df['url_encoding'] = mlb.fit_transform(df['url_domains'])

In [29]:
df

orcid  claimed  verifyed email  \
0         0000-0001-5000-2053     True           False   
1         0000-0001-5000-6548     True           False   
2         0000-0001-5000-7962     True            True   
3         0000-0001-5000-8586     True           False   
4         0000-0001-5001-0256     True           False   
...                       ...      ...             ...   
10747035  0000-0003-4998-1551     True           False   
10747036  0000-0003-4998-4111     True           False   
10747037  0000-0003-4998-6045     True           False   
10747038  0000-0003-4998-8868     True            True   
10747039  0000-0003-4999-7916     True            True   

          verified primary email given names         family name biography  \
0                          False      Jorge   Jaramillo Sanchez       <NA>   
1                          False     Wiseman            Bekelesi      <NA>   
2                           True       ALICE            INDIMULI      <NA>   
3                          False        shim              ji yun      <NA>   
4                          False      Sandro          Caramaschi      <NA>   
...                          ...         ...                 ...       ...   
10747035                   False     Animesh               Ghosh      <NA>   
10747036                   False        Hawa             Liberna      <NA>   
10747037                   False      Tongyi                 Men      <NA>   
10747038                   False    Charldon              Wilken      <NA>   
10747039                    True  Tapas Bapu                B.R.      <NA>   

         other names researcher urls primary email other emails keywords  \
0               <NA>              []                         []       []   
1               <NA>              []                         []       []   
2               <NA>              []                         []       []   
3               <NA>              []                         []       []   
4               <NA>              []                         []       []   
...              ...             ...           ...          ...      ...   
10747035        <NA>              []                         []       []   
10747036        <NA>              []                         []       []   
10747037        <NA>              []                         []       []   
10747038        <NA>              []                         []       []   
10747039        <NA>              []                         []       []   

         external identifiers education employments  number of works  \
0                          []        []          []                0   
1                          []        []          []                0   
2                          []        []          []                0   
3                          []        []          []                0   
4                          []        []          []                0   
...                       ...       ...         ...              ...   
10747035                   []        []          []                0   
10747036                   []        []          []                0   
10747037                   []        []          []                0   
10747038                   []        []          []                0   
10747039                   []        []          []                0   

         works source email_domains url_domains fixed_keywords  
0                  []            []          []             []  
1                  []            []          []             []  
2                  []            []          []             []  
3                  []            []          []             []  
4                  []            []          []             []  
...               ...           ...         ...            ...  
10747035           []            []          []             []  
10747036           []            []          []             []  
10747037           []      